<a href="https://colab.research.google.com/github/garrisongys/SplitFed/blob/main/SFLG_IID.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

# This code is the generalized splitfed learning (SFLG) simulator
# The dataset distribution follows IID in this code
By setting no_of_groups = users, SFLG is the SFLV1. By setting no_of_groups = 1, SFLG is the SFLV2.

## Setting variables

In [ ]:
from google.colab import drive
drive.mount('/content/drive')

Drive already mounted at /content/drive; to attempt to forcibly remount, call drive.mount("/content/drive", force_remount=True).


In [ ]:
rounds = 400
local_epochs = 1 # This has set to be 1 in the SFLG
users = 100 # number of clients 50, 

lr = 0.001

group_client_ordered = True # True means clients are grouped in order -- False means random selection
no_of_groups = 50  # no. of groups/models in the process --- each group has several clients train sequentially at the server


In [ ]:
import os
import h5py

import struct
import pickle
import sys

import torch
import torch.nn as nn
import torch.nn.functional as F
import torch.optim as optim

import time
from tqdm import tqdm
import numpy as np

import pandas
from pandas import DataFrame

from collections import defaultdict
import copy

In [ ]:
# root_path = ''
# model_path = ''
# acc_path = ''

# server_model_path = ''
# client_model_path = ''

# change the yourfolder directory to your own path.
root_path = '/content/drive/My Drive/yourfolder'
model_path = '/content/drive/My Drive/yourfolder/SplitFedComb_IID_model_%dusers_%dcopy.pth'%(users, no_of_groups)
acc_path = '/content/drive/My Drive/yourfolder/SplitFedComb_IID_acc_%dusers_%dcopy.hdf5'%(users, no_of_groups)

server_model_path = '/content/drive/My Drive/yourfolder/SplitFedComb_IID_%dusers_%dcopy.pth'%(users, no_of_groups)
client_model_path = '/content/drive/My Drive/yourfolder/SplitFedComb_IID__%dusers_%dcopy.pth'%(users, no_of_groups)

# root_path = '/content/drive/My Drive/ecgMinki/ecg'
# model_path = '/content/drive/My Drive/ecgMinki/ecg/SplitFedComb_IID/SplitFedComb_IID_model_%dusers_%dcopy.pth'%(users, no_of_groups)
# acc_path = '/content/drive/My Drive/ecgMinki/ecg/SplitFedComb_IID/SplitFedComb_IID_acc_%dusers_%dcopy.hdf5'%(users, no_of_groups)

# server_model_path = '/content/drive/My Drive/ecgMinki/ecg/SplitFedComb_IID/SplitFedComb_IID_%dusers_%dcopy.pth'%(users, no_of_groups)
# client_model_path = '/content/drive/My Drive/ecgMinki/ecg/SplitFedComb_IID/SplitFedComb_IID__%dusers_%dcopy.pth'%(users, no_of_groups)


## Defining `ECG` Dataset Class


In [ ]:
from torch.utils.data import Dataset, DataLoader
from torch.optim import Adam

## Cuda

In [ ]:
device = torch.device("cuda:0" if torch.cuda.is_available() else "cpu")
print(device)

cuda:0


In [ ]:
class ECG(Dataset):
    
    def __init__(self, train=True, choose = -1):
      if train:
        with h5py.File(os.path.join(root_path, 'train_ecg.hdf5'), 'r') as hdf:    # 13245
          # print(len(hdf['y_train'][:]))
          # IID setting
          if choose == -1:
            self.x = hdf['x_train'][:]
            self.x = self.x.reshape(-1, 1, 130)
            self.y = hdf['y_train'][:]
          else:
            num_dataset = int(13245 / users)
            classlist = list(range(num_dataset*choose, num_dataset * (choose+1)))

            self.x = hdf['x_train'][:][classlist]
            self.x = self.x.reshape(-1, 1, 130)
            self.y = hdf['y_train'][:][classlist]

      else:
        with h5py.File(os.path.join(root_path, 'test_ecg.hdf5'), 'r') as hdf:   # 13245
          self.x = hdf['x_test'][:]
          self.x = self.x.reshape(-1, 1, 130)
          self.y = hdf['y_test'][:]
                
    def __len__(self):
        return len(self.x)

    def __getitem__(self, idx):
        return torch.tensor(self.x[idx], dtype=torch.float), torch.tensor(self.y[idx])

## Making Batch Generator

In [ ]:
batch_size = 32

### `DataLoader` for batch generating
`torch.utils.data.DataLoader(dataset, batch_size=1, shuffle=False)`

In [ ]:
train_datasets = []

for i in range(users):
  dataset = ECG(train=True, choose=i)
  train_datasets.append(dataset)
  print("Train Dataset(x_train) Shape: ", train_datasets[i].x.shape)
train_dataset = ECG(train=True)
test_dataset = ECG(train=False)
print("Train Dataset(x_train) Shape: ", train_datasets[i].x.shape)
print("Test Dataset(x_test) Shape: ", test_dataset.x.shape)


Train Dataset(x_train) Shape:  (132, 1, 130)
Train Dataset(x_train) Shape:  (132, 1, 130)
Train Dataset(x_train) Shape:  (132, 1, 130)
Train Dataset(x_train) Shape:  (132, 1, 130)
Train Dataset(x_train) Shape:  (132, 1, 130)
Train Dataset(x_train) Shape:  (132, 1, 130)
Train Dataset(x_train) Shape:  (132, 1, 130)
Train Dataset(x_train) Shape:  (132, 1, 130)
Train Dataset(x_train) Shape:  (132, 1, 130)
Train Dataset(x_train) Shape:  (132, 1, 130)
Train Dataset(x_train) Shape:  (132, 1, 130)
Train Dataset(x_train) Shape:  (132, 1, 130)
Train Dataset(x_train) Shape:  (132, 1, 130)
Train Dataset(x_train) Shape:  (132, 1, 130)
Train Dataset(x_train) Shape:  (132, 1, 130)
Train Dataset(x_train) Shape:  (132, 1, 130)
Train Dataset(x_train) Shape:  (132, 1, 130)
Train Dataset(x_train) Shape:  (132, 1, 130)
Train Dataset(x_train) Shape:  (132, 1, 130)
Train Dataset(x_train) Shape:  (132, 1, 130)
Train Dataset(x_train) Shape:  (132, 1, 130)
Train Dataset(x_train) Shape:  (132, 1, 130)
Train Data

In [ ]:

train_loaders = []
for i in range(users):
  train_loaders.append(DataLoader(train_datasets[i], batch_size=batch_size, shuffle=True))
test_loader = DataLoader(test_dataset, batch_size=batch_size)

## Distribution of clients in the groups -- all clients in the same group unergoes sequential training, and groups undergo fedavg

In [ ]:
group_client_collect_dict = defaultdict(list)
# ordered division of clients in the group: group1 -- client0 to clientx
if group_client_ordered:
    #initialize
    start = 0
    step = int(users/no_of_groups)
    
    diff = users - step* no_of_groups
    #print(diff)
    
    if diff != 0:
        end = step + 1
        diff -= 1
    else:
        end = step
        
    for n in range(no_of_groups):
        
        clients_list = [i for i in range(start, end)]  
        group_client_collect_dict[n]= clients_list
        
        #print("Start, end:",start, end)
        
        if end+step <= users:
            start = copy.deepcopy(end)  
            if diff != 0:
                end += step + 1
                diff -= 1
            else:
                end += step
                
        else:
            start = copy.deepcopy(end)
            end = users
    
else:
    print("program is currently in group_client_ordered mode!")
    

    
    
print(group_client_collect_dict)

defaultdict(<class 'list'>, {0: [0, 1], 1: [2, 3], 2: [4, 5], 3: [6, 7], 4: [8, 9], 5: [10, 11], 6: [12, 13], 7: [14, 15], 8: [16, 17], 9: [18, 19], 10: [20, 21], 11: [22, 23], 12: [24, 25], 13: [26, 27], 14: [28, 29], 15: [30, 31], 16: [32, 33], 17: [34, 35], 18: [36, 37], 19: [38, 39], 20: [40, 41], 21: [42, 43], 22: [44, 45], 23: [46, 47], 24: [48, 49], 25: [50, 51], 26: [52, 53], 27: [54, 55], 28: [56, 57], 29: [58, 59], 30: [60, 61], 31: [62, 63], 32: [64, 65], 33: [66, 67], 34: [68, 69], 35: [70, 71], 36: [72, 73], 37: [74, 75], 38: [76, 77], 39: [78, 79], 40: [80, 81], 41: [82, 83], 42: [84, 85], 43: [86, 87], 44: [88, 89], 45: [90, 91], 46: [92, 93], 47: [94, 95], 48: [96, 97], 49: [98, 99]})


In [ ]:
x_train, y_train = next(iter(train_loaders[0]))
print(x_train.size())
print(y_train.size())

torch.Size([32, 1, 130])
torch.Size([32])


### Number of total batches

In [ ]:
train_total_batch = len(train_loaders[0])
print(train_total_batch)
test_batch = len(test_loader)
print(test_batch)

5
414


In [ ]:
# Dataset size for the serverside -- group wise averaging

datasetsize_server = []
len_dataset = 0
for g in range(no_of_groups):
    for idx in group_client_collect_dict[g]:
        len_dataset += len(train_datasets[idx])
    datasetsize_server.append(len_dataset)
    len_dataset = 0


# Dataset size for the client-size -- client wise averaging   
datasetsize_client = []
for i in range(users):
  datasetsize_client.append(len(train_datasets[i]))

## Pytorch layer modules for *Conv1D* Network



### `Conv1d` layer
- `torch.nn.Conv1d(in_channels, out_channels, kernel_size)`

### `MaxPool1d` layer
- `torch.nn.MaxPool1d(kernel_size, stride=None)`
- Parameter `stride` follows `kernel_size`.

### `ReLU` layer
- `torch.nn.ReLU()`

### `Linear` layer
- `torch.nn.Linear(in_features, out_features, bias=True)`

### `Softmax` layer
- `torch.nn.Softmax(dim=None)`
- Parameter `dim` is usually set to `1`.

## Construct 1D-CNN ECG classification model

In [ ]:
class EcgNet(nn.Module):
    def __init__(self):
        super(EcgNet, self).__init__()        
        self.conv1 = nn.Conv1d(1, 16, 7)  # 124 x 16        
        self.relu1 = nn.LeakyReLU()
        self.pool1 = nn.MaxPool1d(2)  # 62 x 16
        self.conv2 = nn.Conv1d(16, 16, 5)  # 58 x 16
        self.relu2 = nn.LeakyReLU()        
        self.conv3 = nn.Conv1d(16, 16, 5)  # 54 x 16
        self.relu3 = nn.LeakyReLU()        
        self.conv4 = nn.Conv1d(16, 16, 5)  # 50 x 16
        self.relu4 = nn.LeakyReLU()
        self.pool4 = nn.MaxPool1d(2)  # 25 x 16
        self.linear5 = nn.Linear(25 * 16, 128)
        self.relu5 = nn.LeakyReLU()        
        self.linear6 = nn.Linear(128, 5)
        self.softmax6 = nn.Softmax(dim=1)
    
    def forward(self, x):
        x = self.conv1(x)
        x = self.relu1(x)
        x = self.pool1(x)        
        x = self.conv2(x)
        x = self.relu2(x)        
        x = self.conv3(x)
        x = self.relu3(x)        
        x = self.conv4(x)
        x = self.relu4(x)
        x = self.pool4(x)
        x = x.view(-1, 25 * 16)
        x = self.linear5(x)
        x = self.relu5(x)        
        x = self.linear6(x)
        x = self.softmax6(x)
        return x    

In [ ]:
ecg_net = EcgNet()
ecg_net.to(device)

EcgNet(
  (conv1): Conv1d(1, 16, kernel_size=(7,), stride=(1,))
  (relu1): LeakyReLU(negative_slope=0.01)
  (pool1): MaxPool1d(kernel_size=2, stride=2, padding=0, dilation=1, ceil_mode=False)
  (conv2): Conv1d(16, 16, kernel_size=(5,), stride=(1,))
  (relu2): LeakyReLU(negative_slope=0.01)
  (conv3): Conv1d(16, 16, kernel_size=(5,), stride=(1,))
  (relu3): LeakyReLU(negative_slope=0.01)
  (conv4): Conv1d(16, 16, kernel_size=(5,), stride=(1,))
  (relu4): LeakyReLU(negative_slope=0.01)
  (pool4): MaxPool1d(kernel_size=2, stride=2, padding=0, dilation=1, ceil_mode=False)
  (linear5): Linear(in_features=400, out_features=128, bias=True)
  (relu5): LeakyReLU(negative_slope=0.01)
  (linear6): Linear(in_features=128, out_features=5, bias=True)
  (softmax6): Softmax(dim=1)
)

In [ ]:
class EcgClient(nn.Module):
    def __init__(self):
        super(EcgClient, self).__init__()        
        self.conv1 = nn.Conv1d(1, 16, 7)  # 124 x 16        
        self.relu1 = nn.LeakyReLU()
        self.pool1 = nn.MaxPool1d(2)  # 62 x 16
        self.conv2 = nn.Conv1d(16, 16, 5)  # 58 x 16
        self.relu2 = nn.LeakyReLU()        
#         self.conv3 = nn.Conv1d(16, 16, 5)  # 54 x 16
#         self.relu3 = nn.LeakyReLU()        
#         self.conv4 = nn.Conv1d(16, 16, 5)  # 50 x 16
#         self.relu4 = nn.LeakyReLU()
#         self.pool4 = nn.MaxPool1d(2)  # 25 x 16
#         self.linear5 = nn.Linear(25 * 16, 128)
#         self.relu5 = nn.LeakyReLU()        
#         self.linear6 = nn.Linear(128, 5)
#         self.softmax6 = nn.Softmax(dim=1)
    
    def forward(self, x):
        x = self.conv1(x)
        x = self.relu1(x)
        x = self.pool1(x)        
        x = self.conv2(x)
        x = self.relu2(x)        
#         x = self.conv3(x)
#         x = self.relu3(x)        
#         x = self.conv4(x)
#         x = self.relu4(x)
#         x = self.pool4(x)
#         x = x.view(-1, 25 * 16)
#         x = self.linear5(x)
#         x = self.relu5(x)        
#         x = self.linear6(x)
#         x = self.softmax6(x)
        return x        

In [ ]:
ecg_client = EcgClient()
ecg_client.to(device)

EcgClient(
  (conv1): Conv1d(1, 16, kernel_size=(7,), stride=(1,))
  (relu1): LeakyReLU(negative_slope=0.01)
  (pool1): MaxPool1d(kernel_size=2, stride=2, padding=0, dilation=1, ceil_mode=False)
  (conv2): Conv1d(16, 16, kernel_size=(5,), stride=(1,))
  (relu2): LeakyReLU(negative_slope=0.01)
)

In [ ]:
class EcgServer(nn.Module):
    def __init__(self):
        super(EcgServer, self).__init__()        
#         self.conv1 = nn.Conv1d(1, 16, 7)  # 124 x 16        
#         self.relu1 = nn.LeakyReLU()
#         self.pool1 = nn.MaxPool1d(2)  # 62 x 16
#         self.conv2 = nn.Conv1d(16, 16, 5)  # 58 x 16
#         self.relu2 = nn.LeakyReLU()        
        self.conv3 = nn.Conv1d(16, 16, 5)  # 54 x 16
        self.relu3 = nn.LeakyReLU()        
        self.conv4 = nn.Conv1d(16, 16, 5)  # 50 x 16
        self.relu4 = nn.LeakyReLU()
        self.pool4 = nn.MaxPool1d(2)  # 25 x 16
        self.linear5 = nn.Linear(25 * 16, 128)
        self.relu5 = nn.LeakyReLU()        
        self.linear6 = nn.Linear(128, 5)
        self.softmax6 = nn.Softmax(dim=1)
    
    def forward(self, x):
#         x = self.conv1(x)
#         x = self.relu1(x)
#         x = self.pool1(x)        
#         x = self.conv2(x)
#         x = self.relu2(x)        
        x = self.conv3(x)
        x = self.relu3(x)        
        x = self.conv4(x)
        x = self.relu4(x)
        x = self.pool4(x)
        x = x.view(-1, 25 * 16)
        x = self.linear5(x)
        x = self.relu5(x)        
        x = self.linear6(x)
        x = self.softmax6(x)
        return x        

In [ ]:
ecg_server = EcgServer()
ecg_server.to(device)

EcgServer(
  (conv3): Conv1d(16, 16, kernel_size=(5,), stride=(1,))
  (relu3): LeakyReLU(negative_slope=0.01)
  (conv4): Conv1d(16, 16, kernel_size=(5,), stride=(1,))
  (relu4): LeakyReLU(negative_slope=0.01)
  (pool4): MaxPool1d(kernel_size=2, stride=2, padding=0, dilation=1, ceil_mode=False)
  (linear5): Linear(in_features=400, out_features=128, bias=True)
  (relu5): LeakyReLU(negative_slope=0.01)
  (linear6): Linear(in_features=128, out_features=5, bias=True)
  (softmax6): Softmax(dim=1)
)

## variables

In [ ]:
clientsoclist = []
train_total_batch = []

criterion = nn.CrossEntropyLoss()
train_acc = []
val_acc = []
train_lo = []
val_lo = []
train_acc_average=[]

optimizer = Adam(ecg_net.parameters(), lr=lr)
optimizer_client = Adam(ecg_client.parameters(), lr=lr)
optimizer_server = Adam(ecg_server.parameters(), lr=lr)

weights_server_list_group = []
weights_client_list_group = []

## Comunication overhead

In [ ]:
total_sendsize_list = []
total_receivesize_list = []

client_sendsize_list = [[] for i in range(users)]
client_receivesize_list = [[] for i in range(users)]

train_sendsize_list = [] 
train_receivesize_list = []

In [ ]:
import copy

def average_weights(w, datasize):
    """
    Returns the average of the weights.
    """
        
    for i, data in enumerate(datasize):
        for key in w[i].keys():
            w[i][key] *= float(data)
    
    w_avg = copy.deepcopy(w[0])
   
    for key in w_avg.keys():
        for i in range(1, len(w)):
            w_avg[key] += w[i][key]
        w_avg[key] = torch.div(w_avg[key], float(sum(datasize)))


    return w_avg

## Receive users before training

In [ ]:
start_time = time.time()    # store start time
print("timmer start!")
# train()

timmer start!


In [ ]:
def train_client(inputs, labels):

    # zero the parameter gradients
    optimizer_client.zero_grad()

    # forward + backward + optimize
    #----------- Running client side -----------
    outputs = ecg_client(inputs)
    client_output = outputs.clone().detach().requires_grad_(True)
    
    #------------Running server side ------------
    client_grad = train_server(client_output, labels)
    outputs.backward(client_grad)
    optimizer_client.step()    


In [ ]:
def train_server(client_output, labels):
    
    optimizer_server.zero_grad()
    output = ecg_server(client_output)
    loss = criterion(output, labels)
    loss.backward()
    optimizer_server.step()

    return client_output.grad.clone().detach()

## Train

In [ ]:
group_client_weights_collect = []

# global weights at first
global_client_weights = copy.deepcopy(ecg_client.state_dict())
global_server_weights = copy.deepcopy(ecg_server.state_dict())

for r in range(rounds): 
    # initialize the weights of the model for this round
    round_client_weights = copy.deepcopy(global_client_weights)
    
    round_server_weights = copy.deepcopy(global_server_weights)  
    # we will run by groups ----
    for g in range(no_of_groups):
        # for each user in the group g
        #group_client_weights = copy.deepcopy(round_client_weights)
        group_server_weights = copy.deepcopy(round_server_weights)
        
        for u in group_client_collect_dict[g]:
            # model for user u
            #print("User:", u)
            
            # client has the same initial state for the group
            ecg_client.load_state_dict(round_client_weights)
            
            # server model state changes with clients
            ecg_server.load_state_dict(group_server_weights)

            for local_epoch in range(local_epochs):

                for data in tqdm(train_loaders[u], ncols=100, desc='Round'+str(r+1)+': User'+str(u)+'_'+str(local_epoch+1)):
                    # get the inputs; data is a list of [inputs, labels]
                    inputs, labels = data
                    inputs = inputs.to(device)
                    labels = labels.clone().detach().long().to(device)

                    #------------ client forward training -----------
                    optimizer_client.zero_grad()
                    output_client = ecg_client(inputs)
                    client_output = output_client.clone().detach().requires_grad_(True)

                    # ---------- server forward/backward training ------------
                    optimizer_server.zero_grad()
                    output = ecg_server(client_output)
                    loss = criterion(output, labels)
                    loss.backward()
                    optimizer_server.step()
                    client_grad = client_output.grad.clone().detach()

                    # ----------- client backward training ------------
                    output_client.backward(client_grad)
                    optimizer_client.step()
            


            # going for next user in the same group
            client_weights = copy.deepcopy(ecg_client.state_dict())
            group_client_weights_collect.append(client_weights) 
            
            group_server_weights = copy.deepcopy(ecg_server.state_dict())
            
            
        
        # Now going for the different group
        # save the weights of the current model -- current group
        
        weights_server_list_group.append(group_server_weights)
        
        
    # Completion for all groups
    # average
    global_client_weights = average_weights(group_client_weights_collect, datasetsize_client)
    
    global_server_weights = average_weights(weights_server_list_group, datasetsize_server)
    
    weights_server_list_group = []
    group_client_weights_collect = []
        
        
    #==============================================================================================    
    
    
    #================================================================================================================
    # Accuracy check at each round (this is for the gloabl model --- not local model) -------------
    # This is s result for the global model at each round --------
    ecg_client.load_state_dict(global_client_weights)
    ecg_server.load_state_dict(global_server_weights)
    ecg_client.eval()
    ecg_server.eval()
    
    # train acc for each client's training dataset
    # train acc
    with torch.no_grad():
        for u in range(users):
            corr_num = 0
            total_num = 0
            train_loss = 0.0
            for j, trn in enumerate(train_loaders[u]):
                trn_x, trn_label = trn
                trn_x = trn_x.to(device)
                trn_label = trn_label.clone().detach().long().to(device)

                trn_output = ecg_client(trn_x)
                trn_output = ecg_server(trn_output)
                loss = criterion(trn_output, trn_label)
                train_loss += loss.item()
                model_label = trn_output.argmax(dim=1)
                corr = trn_label[trn_label == model_label].size(0)
                corr_num += corr
                total_num += trn_label.size(0)
            train_accuracy = corr_num / total_num * 100
            r_train_loss = train_loss / len(train_loaders[u])
            print("client {}: rounds {}'s train_acc: {:.2f}%, train_loss: {:.4f}".format(u, r + 1, train_accuracy, r_train_loss))
            train_acc.append(train_accuracy)
        avg_acc = sum(train_acc)/len(train_acc)
        print("Train_average accuracy:", avg_acc)
        train_acc_average.append(avg_acc)
        train_acc = []
    # test acc
    with torch.no_grad():
        corr_num = 0
        total_num = 0
        val_loss = 0.0
        for j, val in enumerate(test_loader):
            val_x, val_label = val
            val_x = val_x.to(device)
            val_label = val_label.clone().detach().long().to(device)

            val_output = ecg_client(val_x)
            val_output = ecg_server(val_output)
            loss = criterion(val_output, val_label)
            val_loss += loss.item()
            model_label = val_output.argmax(dim=1)
            corr = val_label[val_label == model_label].size(0)
            corr_num += corr
            total_num += val_label.size(0)
        test_accuracy = corr_num / total_num * 100
        test_loss = val_loss / len(test_loader)
        print("rounds {}'s test_acc: {:.2f}%, test_loss: {:.4f}".format(r + 1, test_accuracy, test_loss))
        val_acc.append(test_accuracy)

end_time = time.time()  # store end time
print("TrainingTime: {} sec".format(end_time - start_time))

Round1: User99_1: 100%|██████████████████████████████████████████████| 5/5 [00:00<00:00, 152.93it/s]


client 0: rounds 1's train_acc: 20.45%, train_loss: 1.6035
client 1: rounds 1's train_acc: 18.18%, train_loss: 1.6095
client 2: rounds 1's train_acc: 24.24%, train_loss: 1.6071
client 3: rounds 1's train_acc: 19.70%, train_loss: 1.6048
client 4: rounds 1's train_acc: 16.67%, train_loss: 1.6079
client 5: rounds 1's train_acc: 21.21%, train_loss: 1.6073
client 6: rounds 1's train_acc: 24.24%, train_loss: 1.6058
client 7: rounds 1's train_acc: 25.00%, train_loss: 1.6064
client 8: rounds 1's train_acc: 18.94%, train_loss: 1.6039
client 9: rounds 1's train_acc: 26.52%, train_loss: 1.6013
client 10: rounds 1's train_acc: 26.52%, train_loss: 1.6024
client 11: rounds 1's train_acc: 25.00%, train_loss: 1.6007
client 12: rounds 1's train_acc: 27.27%, train_loss: 1.6059
client 13: rounds 1's train_acc: 18.18%, train_loss: 1.6050
client 14: rounds 1's train_acc: 20.45%, train_loss: 1.6062
client 15: rounds 1's train_acc: 26.52%, train_loss: 1.6026
client 16: rounds 1's train_acc: 18.94%, train_los

Round2: User6_1:   0%|                                                        | 0/5 [00:00<?, ?it/s]

rounds 1's test_acc: 22.65%, test_loss: 1.6051


Round2: User99_1: 100%|██████████████████████████████████████████████| 5/5 [00:00<00:00, 165.80it/s]


...

client 0: rounds 399's train_acc: 87.88%, train_loss: 1.0451
client 1: rounds 399's train_acc: 91.67%, train_loss: 0.9733
client 2: rounds 399's train_acc: 87.12%, train_loss: 1.0090
client 3: rounds 399's train_acc: 89.39%, train_loss: 1.0374
client 4: rounds 399's train_acc: 81.06%, train_loss: 1.1090
client 5: rounds 399's train_acc: 90.91%, train_loss: 1.0184
client 6: rounds 399's train_acc: 88.64%, train_loss: 1.0425
client 7: rounds 399's train_acc: 90.15%, train_loss: 0.9849
client 8: rounds 399's train_acc: 82.58%, train_loss: 1.0902
client 9: rounds 399's train_acc: 88.64%, train_loss: 1.0405
client 10: rounds 399's train_acc: 93.94%, train_loss: 0.9932
client 11: rounds 399's train_acc: 89.39%, train_loss: 0.9907
client 12: rounds 399's train_acc: 90.15%, train_loss: 0.9908
client 13: rounds 399's train_acc: 90.91%, train_loss: 0.9780
client 14: rounds 399's train_acc: 86.36%, train_loss: 1.1008
client 15: rounds 399's train_acc: 90.91%, train_loss: 0.9791
client 16: rounds 

Round400: User6_1: 100%|█████████████████████████████████████████████| 5/5 [00:00<00:00, 208.32it/s]

rounds 399's test_acc: 88.91%, test_loss: 1.0157



Round400: User99_1: 100%|████████████████████████████████████████████| 5/5 [00:00<00:00, 204.73it/s]


client 0: rounds 400's train_acc: 87.88%, train_loss: 1.0012
client 1: rounds 400's train_acc: 91.67%, train_loss: 0.9747
client 2: rounds 400's train_acc: 88.64%, train_loss: 1.0067
client 3: rounds 400's train_acc: 89.39%, train_loss: 1.0327
client 4: rounds 400's train_acc: 81.06%, train_loss: 1.1762
client 5: rounds 400's train_acc: 92.42%, train_loss: 1.0141
client 6: rounds 400's train_acc: 88.64%, train_loss: 0.9991
client 7: rounds 400's train_acc: 90.15%, train_loss: 0.9859
client 8: rounds 400's train_acc: 82.58%, train_loss: 1.0483
client 9: rounds 400's train_acc: 89.39%, train_loss: 0.9954
client 10: rounds 400's train_acc: 94.70%, train_loss: 0.9512
client 11: rounds 400's train_acc: 89.39%, train_loss: 0.9895
client 12: rounds 400's train_acc: 90.15%, train_loss: 0.9906
client 13: rounds 400's train_acc: 92.42%, train_loss: 0.9792
client 14: rounds 400's train_acc: 86.36%, train_loss: 1.0374
client 15: rounds 400's train_acc: 90.91%, train_loss: 1.0232
client 16: rounds 

## Save accuracy results

In [ ]:
import h5py

with h5py.File(acc_path, "w") as f:
    dset = f.create_dataset("train_acc", data=train_acc)
    dset = f.create_dataset("val_acc", data=val_acc)